In [1]:
import pandas as pd
df = pd.read_json("links.json").dropna()
# df = df[:300]
# df = df[df.link_id == "90f0be68-eadf-4397-a797-4939e7b94859"]

In [2]:
first_road = df.iloc[0]

In [3]:
import folium

def switch_coord(coord):
    return (coord[1], coord[0])

melb_map = folium.Map(location=[-37.82003422345045, 145.01656189422235], zoom_start=17, tiles="cartodb positron")

for i, row in df.iterrows():
    locations = row['polyline']
    locations = [switch_coord(x) for x in locations]
    folium.PolyLine(locations, color='red').add_to(melb_map)
    folium.Marker([row.orig_location[1], row.orig_location[0]], popup=row['orig_id']).add_to(melb_map)
    folium.Marker([row.dest_location[1], row.dest_location[0]], popup=row['dest_id']).add_to(melb_map)

melb_map

In [4]:
import requests

mapbox_token = "sk.eyJ1IjoibWhpbG15IiwiYSI6ImNsc3ZlZDhqYzA5a2kybHMxbzludmJ4cGQifQ.xxLM4e1vUerrbK1rXBb0Dg"

def snap_roads(coordinates):
    coords_str = []
    for (lon, lat) in coordinates:
        coords_str.append("%f,%f" % (lon, lat))
    coord_str = ';'.join(coords_str)
    url = "https://api.mapbox.com/matching/v5/mapbox/driving/%s.json?access_token=%s" % (coord_str, mapbox_token)
    r = requests.get(url)
    data = r.json()
    tracepoints = data['tracepoints']

    polyline = []
    for tracepoint in tracepoints:
        if tracepoint:
            polyline.append(tracepoint['location'])
    return polyline

In [7]:
import traceback
from tqdm import tqdm

snapped_data = []
for i, row in tqdm(df.iterrows()):
    # print("%d out of %d" % (i+1, len(df)))
    pos1 = row['orig_location']
    pos2 = row['dest_location']
    coordinates = [pos1, *row['polyline'], pos2]
    try:
        polyline = snap_roads(coordinates)
        snapped_data.append({
            **row,
            'new_polyline': polyline
        })
        reversed = [switch_coord(x) for x in polyline]
        # folium.PolyLine(reversed, color='green').add_to(melb_map)
    except:
        traceback.print_exc()

df_snapped = pd.DataFrame.from_records(snapped_data)
df_snapped.to_json("snapped_links.json", index=False, orient="records")

2108it [02:01, 17.36it/s]
